Workspace
=========

The core element of a project is the ``Workspace``. A project Workspace holds core information about the author, version and all entities stored in the `geoh5` file. It also knows how to create the core structure needed by [Geoscience ANALYST](https://mirageoscience.com/mining-industry-software/geoscience-analyst/) for visualization.

![workspace](./images/workspace.png)


## Creation

You can create a blank workspace with the `.create` method

In [1]:
from pathlib import Path

from geoh5py.workspace import Workspace


# Create a new project
workspace = Workspace.create("project.geoh5")

![blankworkspace](./images/blankworkspace.png){width="50%"}

Et voila!

## Opening and closing

You can open an existing project by simply entering the desired file name on instantiation of the `Workspace` object.

In [2]:
workspace = Workspace("project.geoh5")

If the `geoh5` file already exists on disk, the API will open the file and import the tree structure.

> **Deprecation Warning**
> In future releases, the implicite creation of a new Workspace from a file path will be deprecated. Users will be required
> to use the `save()` method to explicitely write a file to disk.

By default, the `*.geoh5` file is accessed in "read-write" mode. In the eventuality that the file is already used by Geoscience ANALYST, the mode gets changed to "read-only". This prevents users from modifying the file while used in an active session, but still allows them to extract data from the workspace. The same restriction does not apply to multiple python processes, as permitted by the `Single Writer Multiple Reader (SWMR)` feature of HDF5.

In [3]:
print(workspace.geoh5)

<HDF5 file "project.geoh5" (mode r+)>


After completing the read/write process, the workspace must be closed in order to release the file. Geoscience ANALYST does not allow reading on an opened file.

In [4]:
workspace.close()

print(workspace._geoh5)

<Closed HDF5 file>


## Context manager

Likewise, a workspace can be accessed via a context manager (the prefered way), which will handle closing the file at the of a process.

In [5]:
with Workspace("project.geoh5") as workspace:
    print(workspace.geoh5)

print(workspace._geoh5)

<HDF5 file "project.geoh5" (mode r+)>
<Closed HDF5 file>


## In-memory

Starting from v0.8.0, it is possible to interact with a `Workspace` in memory. Users can omit to provide a path to an `h5file`, in which case the project is save as a `io.BytesIO` object. 

In [6]:
in_memory = Workspace()
print(in_memory.h5file)

Likewise, an existing `geoh5` project stored as `io.BytesIO` can be provided directly. The example below shows how to read a `geoh5` as a raw byte object, then converted to a `io.BytesIO` object.

In [7]:
from io import BytesIO


with open("project.geoh5", "rb") as in_file:
    byte_data = in_file.read()

bytes_ws = Workspace(BytesIO(byte_data))

print(bytes_ws.h5file)

The `save` method can be used to convert the in-memory project to a file on disk. Users must provide a file name with path.

In [8]:
bytes_ws.save("./new_project.geoh5")

After saving to disk, the `h5file` attribute is converted to a `Path` with reference to the `geoh5` structure on disk.

In [9]:
print(bytes_ws.h5file)

new_project.geoh5


In [10]:
bytes_ws.close()